# Welcome

This notebook serves as an example to how we can create neighbourhood boundaries in the context of transportation for the UK. Any issues, please contact me at b8008458@newcastle.ac.uk!

We begin with importing the necessary libraries. There should be a .yml file on the GitHub repository which can be used to set up the correct environment. We also update OSMNx to ensure all the OSM tags we need are avaiable and ready. 

In [20]:
# Library imports
import geopandas as gpd
import osmnx as ox
import networkx as nx
import momepy
from shapely import Polygon
import matplotlib.pyplot as plt
import folium
import pandas as pd
import overpy
from shapely.geometry import LineString
from shapely.geometry import Point
import requests
from shapely.geometry import MultiPolygon

In [21]:
# update osmnx settings
useful_tags_ways = ox.settings.useful_tags_way + ['cycleway'] + ['bicycle'] + ['motor_vehicle'] + ['railway'] + ['tunnel'] + ['barrier'] + ['bus'] + ['access'] + ['oneway'] + ['oneway:bicycle'] + ['covered'] + ['waterway']
ox.config(use_cache=True, 
          log_console=True,
          useful_tags_way=useful_tags_ways
          )

C:\Users\b8008458\AppData\Local\Temp\ipykernel_12224\305956182.py:3: UserWarning: The `utils.config` function is deprecated and will be removed in a future release. Instead, use the `settings` module directly to configure a global setting's value. For example, `ox.settings.log_console=True`.
  ox.config(use_cache=True,


This project mostly uses OpenStreetMap data. However, the road data provided by the Ordance Survey is of a higher quality for a portion of this project. You will need to access the OSOpenRoads dataset from Ordance Survey, which can be found at https://osdatahub.os.uk/downloads/open/OpenRoads. Please note that it is only avaiable for educuational and academic projects. You will need to set the file path yourself.

In [22]:
# read in UK road gpkg
#os_open_roads = gpd.read_file(r"C:\Users\b8008458\OneDrive - Newcastle University\2022 to 2023\PhD\ltnDetection\LTN-Detection\data\oproad_gpkg_gb\Data\oproad_roads_only.gpkg")

Now we set the location of our example area. Feel free to try your own place (provided it is within the UK)

In [23]:
# set place
place = "Newcastle Upon Tyne, United Kingdom"

We can now get all of the bounding features for our neighbourhoods. This covers railways, rivers, busy bus routes, roads (based on road type) and landuse.

In [24]:
# boundary

boundary = ox.geocode_to_gdf(place)
boundary = boundary.to_crs('EPSG:27700')

# buffer boundary to ensure clips include riverlines which may act as borders between geographies
boundary_buffered = boundary.buffer(50)

In [25]:
## get railways

# for unknown reasons, using rail = ox.graph_from_place(place, custom_filter='["railway"]')
# doesn't ALWAYS retrive the full rail network, hence why multiple lines are used to achive the same result

# Get the major rail network
railway_types = ["","rail", "light_rail", "narrow_gauge", "subway", "tram"]

# set an empty
combined_railways = nx.MultiDiGraph()

for railway_type in railway_types:
    try:
        network = ox.graph_from_place(place, simplify=False 
                                      , custom_filter=f'["railway"~"{railway_type}"]'
                                      )
    
    # handle locations where not all rail types are found
    except Exception as e:
        print(f"No railway data found for '{railway_type}'.")
        network = nx.MultiGraph()

    combined_railways = nx.compose(combined_railways, network)
    


# convert to gdf
railways = ox.graph_to_gdfs(combined_railways, nodes=False, edges=True)




# Drop any other railway types that aren't needed
railways = railways.loc[(~railways["railway"].isin(["tunnel", "abandoned", "razed", "disused", "funicular", "monorail", "miniature"]))]


# Drop rows where any of the specified columns have values "True" or "yes"
columns_to_check = ['tunnel', 'abandoned', 'razed', 'disused', 'funicular', 'monorail', 'miniature']
railways = railways.loc[~railways[railways.columns.intersection(columns_to_check)].isin(['True', 'yes']).any(axis=1)]


# set railways crs
railways = railways.to_crs('EPSG:27700')

No railway data found for 'narrow_gauge'.
No railway data found for 'subway'.
No railway data found for 'tram'.


In [7]:
## get rivers

# reset boundary crs to allow for features to be found
boundary_buffered = boundary_buffered.to_crs('EPSG:4326')


tags = {"waterway": ["river", "rapids"]}

rivers = ox.features_from_polygon(polygon = boundary_buffered.iloc[0], tags = tags)

# Dropping rows where 'tunnel' is equal to 'culvert'
if 'tunnel' in rivers.columns:
    # Dropping rows where 'tunnel' is equal to 'culvert'
    rivers = rivers[rivers['tunnel'] != 'culvert']

# set/reset crs
rivers = rivers.to_crs('27700')
boundary_buffered = boundary_buffered.to_crs('27700')

In [8]:
## get unsuitable landcover types

# reset boundary crs to allow for features to be found
boundary_buffered = boundary_buffered.to_crs('EPSG:4326')

# Define tags
tags = {"landuse": ["industrial", "railway", "brownfield", "commercial", "farmland", "meadow"]}

# Use ox.features_from_polygon to find features matching the specified tags
landuse = ox.features_from_polygon(polygon = boundary_buffered.iloc[0], tags = tags)

# set/reset crs
landuse = landuse.to_crs('27700')

## get unsuitable "nature" types

# Define tags
tags = {"natural": ["wood", "water", "scrub"]}

# Use ox.features_from_polygon to find features matching the specified tags
nature = ox.features_from_polygon(polygon = boundary_buffered.iloc[0], tags = tags)

# set/reset crs
nature = nature.to_crs('27700')

## get unsuitable "lesiure" types. This is mainly for golfcourses

# Define tags
tags = {"leisure": ["golf_course", "track", "park"]}

# Use ox.features_from_polygon to find features matching the specified tags
leisure = ox.features_from_polygon(polygon = boundary_buffered.iloc[0], tags = tags)

# set/reset crs
leisure = leisure.to_crs('27700')
boundary_buffered = boundary_buffered.to_crs('27700')

def retrieve_osm_features(polygon, tags):
    try:
        features = ox.features_from_polygon(polygon=polygon, tags=tags)
    except Exception as e:
        error_message = str(e)
        if "There are no data elements in the server response" in error_message:
            print("No data elements found for the specified location/tags.")
            features = gpd.GeoDataFrame()  # Create an empty GeoDataFrame
        else:
            # Handle other exceptions here if needed
            print("An error occurred:", error_message)
            features = None
    return features

# Define the tags for aeroway
aeroway_tags = {"aeroway": ["aerodrome"]}

# Use the function to retrieve aeroway features
aeroway = retrieve_osm_features(polygon=boundary_buffered.iloc[0], tags=aeroway_tags)

# Check if any features were retrieved
if aeroway is not None:
    if not aeroway.empty:
        # set/reset crs
        aeroway = aeroway.to_crs('27700')

# concat
landuse = pd.concat([landuse, nature, leisure, aeroway])



In [9]:
## get bus routes from OSM/NAPTAN

# reset boundary crs to allow for features to be found
boundary_buffered = boundary_buffered.to_crs('EPSG:4326')

# Calculate the bounding box for XML query
bounding_box = boundary_buffered.bounds

# Extract the minimum and maximum coordinates
minx = bounding_box['minx'].min()
miny = bounding_box['miny'].min()
maxx = bounding_box['maxx'].max()
maxy = bounding_box['maxy'].max()

# Create a list of four elements representing the bounding box
bbox = [minx, miny, maxx, maxy]

# reset boundary_buffer crs
boundary_buffered = boundary_buffered.to_crs('27700')

# Define the Overpass API endpoint
overpass_url = "https://overpass-api.de/api/interpreter"

# Define the XML query
xml_query = f"""
<osm-script output="json" output-config="" timeout="160">
  <union into="_">
    <query into="_" type="node">
      <has-kv k="route" modv="" v="bus"/>
      <bbox-query s="{bbox[1]}" w="{bbox[0]}" n="{bbox[3]}" e="{bbox[2]}" />
    </query>
    <query into="_" type="way">
      <has-kv k="route" modv="" v="bus"/>
      <bbox-query s="{bbox[1]}" w="{bbox[0]}" n="{bbox[3]}" e="{bbox[2]}" />
    </query>
    <query into="_" type="relation">
      <has-kv k="route" modv="" v="bus"/>
      <bbox-query s="{bbox[1]}" w="{bbox[0]}" n="{bbox[3]}" e="{bbox[2]}" />
    </query>
  </union>
  <print e="" from="_" geometry="full" ids="yes" limit="" mode="body" n="" order="id" s="" w=""/>
  <recurse from="_" into="_" type="down"/>
  <print e="" from="_" geometry="full" ids="yes" limit="" mode="skeleton" n="" order="quadtile" s="" w=""/>
</osm-script>

"""
# Initialize lists to store data
geometries = []
element_data = []

# Make the Overpass API request
response = requests.post(overpass_url, data=xml_query)

# Check if the request was successful
if response.status_code == 200:
    data = response.json()
    
    # Access the data from the response
    for element in data.get("elements", []):
        if element.get('type') == 'way' and 'geometry' in element:
            # Extract geometry coordinates from 'geometry' field
            coordinates = [(node['lon'], node['lat']) for node in element['geometry']]
            # Create a LineString geometry
            line = LineString(coordinates)
            geometries.append(line)
            element_data.append(element)

    # Create a GeoDataFrame
    bus_routes = gpd.GeoDataFrame(element_data, geometry=geometries)

    # Set CRS
    bus_routes = bus_routes.set_crs('4326')
    bus_routes = bus_routes.to_crs('27700')

else:
    print(f"Error fetching data: {response.status_code} - {response.text}")

In [10]:
## clip roads, rivers and railways to boundary

# clip
os_open_roads_clip = gpd.clip(os_open_roads, boundary_buffered)
rivers_clip = gpd.clip(rivers, boundary_buffered)
railways_clip = gpd.clip(railways, boundary_buffered)
landuse_clip = gpd.clip(landuse, boundary_buffered)
bus_routes_clip = gpd.clip(bus_routes, boundary_buffered)

In [11]:
## count bus routes per road and remove roads with greater than 1 bus route on them

# set a buffer distance to convert roads to polygons
buffer_distance = 0.2  # Adjust this value as needed. Set in meters

# Create a new GeoDataFrame with the buffered geometries
bus_routes_buffered = bus_routes_clip.copy()  # Copy the original GeoDataFrame
bus_routes_buffered['geometry'] = bus_routes_buffered['geometry'].buffer(buffer_distance)

# count the number of overlapping bus routes
def count_overlapping_features(gdf):
    # Create an empty column to store the count of overlapping features
    gdf['Bus_routes_count'] = 0

    # Iterate through each row in the GeoDataFrame
    for idx, row in gdf.iterrows():
        # Get the geometry of the current row
        geometry = row['geometry']
        
        # Use a spatial filter to find overlapping features
        overlaps = gdf[gdf['geometry'].intersects(geometry)]
        
        # Update the Bus_routes_count column with the count of overlapping features
        gdf.at[idx, 'Bus_routes_count'] = len(overlaps)
    
    return gdf

# call function
bus_routes_buffered_with_count = count_overlapping_features(bus_routes_buffered)

# drop any roads which have less than two bus routes on them

bus_routes_clip = bus_routes_buffered_with_count[bus_routes_buffered_with_count['Bus_routes_count'] >= 2]


In [12]:
# Find "boundary" roads
boundary_roads = os_open_roads_clip.loc[((os_open_roads_clip['primary_route'] == 'True') |
                        (os_open_roads_clip['trunk_road'] == 'True') |
                        (os_open_roads_clip['fictitious'] == 'True') |
                        (os_open_roads_clip['road_classification'] == 'A Road') | 
                        (os_open_roads_clip['road_classification'] == 'B Road') | 
                        #(os_open_roads_clip['road_function'] == 'Restricted Local Access Road') |
                        (os_open_roads_clip['road_function'] == 'Minor Road') |
                        (os_open_roads_clip['road_function'] == 'Motorway') |
                        (os_open_roads_clip['road_function'] == 'Minor Road')  
                        )]

In [13]:
## buffer and dissolve 
 
def buffer_and_dissolve(input_gdf):
    # Buffer around boundaries
    buffered_gdf = input_gdf.copy()  # Create a copy to avoid modifying the original
    buffered_gdf['geometry'] = buffered_gdf['geometry'].buffer(5) # set a 5 meter buffer

    # Dissolve the geometries
    dissolved_geo = buffered_gdf.unary_union

    # Create a new GeoDataFrame with the dissolved geometry
    dissolved_gdf = gpd.GeoDataFrame(geometry=[dissolved_geo])

    # Set the CRS (Coordinate Reference System)
    dissolved_gdf.crs = input_gdf.crs

    return dissolved_gdf

def dissolve_gdf(input_gdf):
    # dissolve geometries
    dissolved_geo = input_gdf.unary_union
    dissolved_gdf = gpd.GeoDataFrame(geometry=[dissolved_geo])
    dissolved_gdf.crs = input_gdf.crs

    return dissolved_gdf



# buffer and dissolve 

boundary_roads_bd = buffer_and_dissolve(boundary_roads)
boundary_rivers_bd = buffer_and_dissolve(rivers_clip)
boundary_rail_bd = buffer_and_dissolve(railways_clip)
boundary_landuse_bd = buffer_and_dissolve(landuse_clip)
boundary_bus_routes_bd = buffer_and_dissolve(bus_routes_clip)

To view any single bounding feature type, use the .explore() method.

In [14]:
# example explore
#boundary_roads_bd.explore()
#boundary_rivers_bd.explore() 
boundary_rail_bd.explore() 
#boundary_landuse_bd.explore()
#boundary_bus_routes_bd.explore()

We then join the boundary features together, erase them from the study area boundary and clean the resulting polygons

In [15]:
# join all boundary features

boundaries = pd.concat([boundary_rivers_bd 
                        ,boundary_roads_bd 
                        ,boundary_rail_bd 
                        ,boundary_landuse_bd
                        ,boundary_bus_routes_bd
                        ], ignore_index=True)
boundary_features = dissolve_gdf(boundaries)

# Use the `difference` method to perform the "Erase" operation
erased_boundary = boundary.difference(boundary_features.unary_union)

# Convert the GeoSeries to a single geometry using unary_union
erased_boundary = erased_boundary.unary_union

# Create a new GeoDataFrame with the result of "Erase" operation
erased_boundary_gdf = gpd.GeoDataFrame(geometry=[erased_boundary], crs=boundary.crs)

# explode multipolygon to polygons
erased_boundary_gdf = erased_boundary_gdf.explode()

neighbourhoods = erased_boundary_gdf

## drop very small areas (such as the centre of roundabouts etc)

# calculate area
neighbourhoods["area"] = neighbourhoods.geometry.area
# Drop rows where area is less than 5000. This value is arbitary
neighbourhoods = neighbourhoods.loc[neighbourhoods["area"] >= 10000]


## drop areas with no roads


def count_roads_within_polygons(polygons_gdf, roads_gdf, polygon_column_name):
    """
    Count the number of roads within each polygon in a GeoDataFrame.
    
    Args:
        polygons_gdf (GeoDataFrame): GeoDataFrame containing polygons.
        roads_gdf (GeoDataFrame): GeoDataFrame containing roads.
        polygon_column_name (str): Name of the column in polygons_gdf to use for grouping.

    Returns:
        GeoDataFrame: Original polygons GeoDataFrame with a "road_count" column added.
    """
    
    # spatial join
    joined = gpd.sjoin(polygons_gdf, roads_gdf, how='left', op='intersects')
    
    # Group by the polygon column and count the number of roads in each
    road_counts = joined.groupby(polygon_column_name).size().reset_index(name='road_count')
    
    # Merge the road counts back into the polygons GeoDataFrame
    polygons_gdf = polygons_gdf.merge(road_counts, on=polygon_column_name, how='left')

     # Calculate road density (area divided by road_count). It is mulitiplied by 10000 for ease of understanding the numbers involved with this
    polygons_gdf['road_density'] = (polygons_gdf['road_count'] / polygons_gdf['area'] ) * 10000
    
    return polygons_gdf

neighbourhoods = count_roads_within_polygons(neighbourhoods, os_open_roads_clip, 'geometry')

# Drop rows with road_density below 0.2 or less than 4 roads
neighbourhoods = neighbourhoods[(neighbourhoods['road_count'] > 2)]
neighbourhoods = neighbourhoods[(neighbourhoods['road_density'] > 0.2)]


## create unique IDs

# simple number based ID
neighbourhoods['ID'] = range(1, len(neighbourhoods) + 1)



## remove holes from neighbourhoods (for visual reasons mostly)



# Function to remove holes from neighbourhoods
def remove_holes(polygon):
    if polygon.geom_type == 'Polygon':
        return Polygon(polygon.exterior)
    else:
        return polygon

# Apply the function to the 'geometry' column of the GeoDataFrame
neighbourhoods['geometry'] = neighbourhoods['geometry'].apply(remove_holes)



## we also need to join the length of the streets within the neighbourhood for further analysis

# Reset index of neighbourhoods
neighbourhoods = neighbourhoods.reset_index(drop=True)

# Perform a spatial join
joined_data = gpd.sjoin(os_open_roads_clip, neighbourhoods, how="inner", op="intersects")

# Group by neighborhood and calculate total road length
road_lengths = joined_data.groupby('index_right')['length'].sum().reset_index()

# Merge road_lengths with neighbourhoods and drop 'index_right' column
neighbourhoods = neighbourhoods.merge(road_lengths, left_index=True, right_on='index_right', how='left').drop(columns=['index_right'])

# Rename the column
neighbourhoods.rename(columns={'length': 'road_lengths'}, inplace=True)


C:\Users\b8008458\AppData\Local\Temp\ipykernel_12224\2215471136.py:21: FutureWarning: Currently, index_parts defaults to True, but in the future, it will default to False to be consistent with Pandas. Use `index_parts=True` to keep the current behavior and True/False to silence the warning.
  erased_boundary_gdf = erased_boundary_gdf.explode()
c:\Users\b8008458\Anaconda3\envs\ox_151\Lib\site-packages\IPython\core\interactiveshell.py:3505: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\Users\b8008458\Anaconda3\envs\ox_151\Lib\site-packages\IPython\core\interactiveshell.py:3445: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if await self.run_code(code, result, async_=asy):


In [16]:
neighbourhoods.explore()

We now have the neighbourhood boundaries we will use in our later analysis :) 

Optionally, we can now export the neighbourhoods to a geopackage for later use. 

In [17]:
neighbourhoods

geometry           area  \
0    POLYGON ((404749.841 411250.562, 404749.822 41...   41754.522573   
1    POLYGON ((404835.587 411288.411, 404836.091 41...   63055.628337   
2    POLYGON ((404810.371 411545.470, 404810.820 41...   15954.081315   
3    POLYGON ((404433.731 411607.694, 404411.711 41...   43928.417723   
4    POLYGON ((405274.659 411579.593, 405275.000 41...   38784.038339   
..                                                 ...            ...   
658  POLYGON ((426150.881 423078.705, 426151.142 42...   95760.527591   
659  POLYGON ((425337.380 424072.603, 425337.502 42...  145611.507063   
660  POLYGON ((426008.766 424300.736, 426008.365 42...   45611.012019   
661  POLYGON ((425133.565 424762.283, 425133.593 42...  315842.211347   
662  POLYGON ((426923.089 424451.087, 426916.678 42...   63818.082937   

     road_count  road_density   ID  road_lengths  
0            12      2.873940    1         854.0  
1            23      3.647573    2        1876.0  
2            11      6.894787    3         524.0  
3             8      1.821145    4         613.0  
4            11      2.836218    5         750.0  
..          ...           ...  ...           ...  
658           4      0.417709  659         639.0  
659          35      2.403656  660        3085.0  
660           3      0.657736  661         224.0  
661          63      1.994667  662        5829.0  
662           4      0.626782  663         586.0  

[663 rows x 6 columns]

In [18]:
## export neighbourhoods

# send to geopackage 
geometry_column = neighbourhoods.geometry.name

# Iterate through the columns and convert them to strings

for column in neighbourhoods.columns:
    if column != geometry_column:
        neighbourhoods[column] = neighbourhoods[column].astype(str)
neighbourhoods.to_file(r'C:\Users\b8008458\Documents\scratch_space\neighbourhoods.gpkg', driver="GPKG")